# **Azure ADLS GEN2**

In [0]:
spark.conf.set(
  "fs.azure.account.key.tnelectionanalytics.dfs.core.windows.net",
  "********K0YWjaEyvFF+Sw9/wd3v1f0f1ZGXQU5tw7PoyoLuH+J/4lnvRh/DHwANAv09*********=="
)


In [0]:
configs = {
  "fs.azure.account.key.tnelectionanalytics.blob.core.windows.net":
  "********K0YWjaEyvFF+Sw9/wd3v1f0f1ZGXQU5tw7PoyoLuH+J/4lnvRh/DHwANAv09*********=="
}

**Mounting the folders**

In [0]:
dbutils.fs.mount(
  source = "wasbs://raw@tnelectionanalytics.blob.core.windows.net/",
  mount_point = "/mnt/elections_raw",
  extra_configs = configs
)

True

In [0]:
display(dbutils.fs.ls("/mnt/elections_raw"))

path name size modificationTime dbfs:/mnt/elections_raw/elections/ elections/ 0 0

In [0]:
dbutils.fs.mount(
  source = "wasbs://curated@tnelectionanalytics.blob.core.windows.net/",
  mount_point = "/mnt/elections_curated",
  extra_configs = configs
)

True

In [0]:
# Check the root of the DBFS
dbutils.fs.ls("/mnt/") 



[FileInfo(path='dbfs:/mnt/elections_curated/', name='elections_curated/', size=0, modificationTime=0),
 FileInfo(path='dbfs:/mnt/elections_raw/', name='elections_raw/', size=0, modificationTime=0)]

In [0]:
%fs ls /mnt/elections_raw/elections/

path name size modificationTime dbfs:/mnt/elections_raw/elections/1971.csv 1971.csv 16902 1765314908000 dbfs:/mnt/elections_raw/elections/1977.csv 1977.csv 25725 1765314908000 dbfs:/mnt/elections_raw/elections/1980.csv 1980.csv 26592 1765314909000 dbfs:/mnt/elections_raw/elections/1984.csv 1984.csv 26426 1765314909000 dbfs:/mnt/elections_raw/elections/1989.csv 1989.csv 25209 1765314909000 dbfs:/mnt/elections_raw/elections/1991.csv 1991.csv 26775 1765314909000 dbfs:/mnt/elections_raw/elections/1996.csv 1996.csv 28353 1765314909000 dbfs:/mnt/elections_raw/elections/2001.csv 2001.csv 28772 1765314909000 dbfs:/mnt/elections_raw/elections/2006.csv 2006.csv 27330 1765314909000 dbfs:/mnt/elections_raw/elections/2011.csv 2011.csv 32222 1765314909000 dbfs:/mnt/elections_raw/elections/2016.csv 2016.csv 31317 1765314909000 dbfs:/mnt/elections_raw/elections/2021.csv 2021.csv 30648 1765314909000 dbfs:/mnt/elections_raw/elections/TN Bye-Elections .csv TN Bye-Elections .csv 3627 1765314909000

**Cleaning the Raw to bronze data**

In [0]:
files = [
    "dbfs:/mnt/elections_raw/elections/1971.csv",
    "dbfs:/mnt/elections_raw/elections/1977.csv",
    "dbfs:/mnt/elections_raw/elections/1980.csv",
    "dbfs:/mnt/elections_raw/elections/1984.csv",
    "dbfs:/mnt/elections_raw/elections/1989.csv",
    "dbfs:/mnt/elections_raw/elections/1991.csv",
    "dbfs:/mnt/elections_raw/elections/1996.csv",
    "dbfs:/mnt/elections_raw/elections/2001.csv",
    "dbfs:/mnt/elections_raw/elections/2006.csv"
]

from pyspark.sql.types import *
from pyspark.sql.functions import regexp_replace, col, lit, regexp_extract, round

# Define schema
election_schema = StructType([
    StructField("ac_name", StringType(), True),
    StructField("ac_no", LongType(), True),
    StructField("type", StringType(), True),
    StructField("winning_cand", StringType(), True),
    StructField("party", StringType(), True),
    StructField("totelectors", StringType(), True),
    StructField("totvotes", StringType(), True),
    StructField("poll_percentage", StringType(), True),
    StructField("margin", StringType(), True),
    StructField("winning_percentage", StringType(), True)
])

df = spark.read.option("header", True).schema(election_schema).csv(files)

#remove records when all the columns are empty
df = df.na.drop(how='all')

df = (
    df.withColumn("totelectors", regexp_replace(col("totelectors"), ",", "").cast("long"))
       .withColumn("totvotes", regexp_replace(col("totvotes"), ",", "").cast("long"))
       .withColumn("margin", regexp_replace(col("margin"), ",", "").cast("long"))
       .withColumn("poll_percentage", round(regexp_replace(col("poll_percentage"), "%", "").cast("float")).cast("long"))
       .withColumn("winning_percentage", round(regexp_replace(col("winning_percentage"), "%", "").cast("float")).cast("long"))
)

# Insert 'district' column between 'type' and 'winning_cand'
cols = df.columns
insert_at = cols.index("type") + 1
new_cols = cols[:insert_at] + ["district"] + cols[insert_at:]
df = df.withColumn("district", lit(None).cast(StringType())).select(*new_cols)

# Add filename (year) as int as the first column, extracting 4 digits before .csv
df = df.withColumn(
    "filename",
    regexp_extract(col("_metadata.file_name"), r"(\d{4})\.csv$", 1).cast("int")
).select("filename", *df.columns)

display(df)

filename ac_name ac_no type district winning_cand party totelectors totvotes poll_percentage margin winning_percentage 2001 Royapuram 1 GEN null Jayakumar.D All India Anna Dravida Munnetra Kazhagam 156528 78338 50 13712 18 2001 Harbour 2 GEN null Anbazhagan.K Dravida Munetra Kazhagam 129157 51563 40 336 1 2001 Dr. Radhakrishnan Nagar 3 GEN null Sekar Babu.P.K All India Anna Dravida Munnetra Kazhagam 272666 128175 47 27332 21 2001 Park Town 4 GEN null Vinayakamurthi S.G Tamil Maanila Congress (MOOPANAR) 140145 64268 46 6377 10 2001 Perambur 5 SC null Mahendran K. Communist Party Of India (MARXIST) 276886 132799 48 17223 13 2001 Purasawalkam 6 GEN null Ranganathan B Dravida Munetra Kazhagam 307376 143574 47 3802 3 2001 Egmore 7 SC null Parithi.Ellamvazhuthi Dravida Munetra Kazhagam 155310 69590 45 86 0 2001 Anna Nagar 8 GEN null Arcot Veeraswami .N Dravida Munetra Kazhagam 376745 160469 43 5578 4 2001 Theagaraya Nagar 9 GEN null Anbazhagan.J Dravida Munetra Kazhagam 277999 119216 43 2499 2 2001 Thousand Lights 10 GEN null Stalin M.K. Dravida Munetra Kazhagam 210474 95428 45 7274 8 2001 Chepauk 11 GEN null Karunanidhi M Dravida Munetra Kazhagam 128399 57477 45 4834 8 2001 Triplicane 12 GEN null Hussain.S.A.M. Dravida Munetra Kazhagam 162839 70179 43 3676 5 2001 Mylapore 13 GEN null Lakshmanan.K.N Bharatiya Janta Party 288708 119385 41 6047 5 2001 Saidapet 14 GEN null Perumal.V Dravida Munetra Kazhagam 279266 129080 46 3881 3 2001 Gummidipundi 15 GEN null Sudarsanam.K. All India Anna Dravida Munnetra Kazhagam 209468 131096 63 24958 19 2001 Ponneri 16 SC null Kannan.A.S. Communist Party Of India 243530 149148 61 27390 18 2001 Thiruvottiyur 17 GEN null Arumugam.T All India Anna Dravida Munnetra Kazhagam 432947 207167 48 34041 16 2001 Villivakkam 18 GEN null Nepoleon .D Dravida Munetra Kazhagam 819547 341837 42 9230 3 2001 Alandur 19 GEN null Valarmathi B. All India Anna Dravida Munnetra Kazhagam 423174 198708 47 12596 6 2001 Tambaram 20 GEN null Vaidialingam M.A. Dravida Munetra Kazhagam 776058 322120 42 5431 2 2001 Tirupporur 21 SC null Kanitha Sampath S All India Anna Dravida Munnetra Kazhagam 235443 136750 58 24790 18 2001 Chengalpattu 22 GEN null Arumugam K Pattali Makkal Katchi 204010 120628 59 5149 4 2001 Maduranthakam 23 GEN null Vasudevan .P. All India Anna Dravida Munnetra Kazhagam 181901 112755 62 11694 10 2001 Acharapakkam 24 SC null Selvaraj.A Pattali Makkal Katchi 167541 100793 60 15478 15 2001 Uthiramerur 25 GEN null Somasundaram. V All India Anna Dravida Munnetra Kazhagam 196375 130726 67 27622 21 2001 Kancheepuram 26 GEN null Thirunavukkarasu Ss All India Anna Dravida Munnetra Kazhagam 251748 150954 60 23603 16 2001 Sriperumbudur 27 SC null Yasodha D Indian National Congress 222968 141515 63 17193 12 2001 Poonamallee 28 GEN null Shanmugam S Pattali Makkal Katchi 306344 165864 54 2316 1 2001 Tiruvallur 29 GEN null Sudharsanam.D Tamil Maanila Congress (MOOPANAR) 193411 111789 58 19951 18 2001 Tiruttani 30 GEN null Raviraj G Pattali Makkal Katchi 173980 117063 67 13874 12 2001 Pallipet 31 GEN null Narasimhan .P.M All India Anna Dravida Munnetra Kazhagam 183742 126049 69 28240 22 2001 Arkonam 32 SC null Bhavani Karunakaran .K All India Anna Dravida Munnetra Kazhagam 191523 121695 64 20256 17 2001 Sholinghur 33 GEN null Vilvanathan. R All India Anna Dravida Munnetra Kazhagam 175100 124842 71 9795 8 2001 Ranipet 34 GEN null Chandrasekaran M.S. All India Anna Dravida Munnetra Kazhagam 227057 147771 65 24963 17 2001 Arcot 35 GEN null Neelakandan P All India Anna Dravida Munnetra Kazhagam 160346 111012 69 17707 16 2001 Katpadi 36 GEN null Duraimurugan Dravida Munetra Kazhagam 193925 129854 67 8002 6 2001 Gudiyatham 37 GEN null Suryakala C.M. All India Anna Dravida Munnetra Kazhagam 164937 107193 65 24324 23 2001 Pernambut 38 SC null Kanagathara (Selvi). C All India Anna Dravida Munnetra Kazhagam 181724 110704 61 28855 26 2001 Vaniayambadi 39 GEN null Abdul Latheef. M. Independent 194773 112346 58 11938 11 2001 Natrampalli 40 

In [0]:
files = [
    "dbfs:/mnt/elections_raw/elections/2011.csv",
    "dbfs:/mnt/elections_raw/elections/2016.csv",
    "dbfs:/mnt/elections_raw/elections/2021.csv"
]

from pyspark.sql.types import *
from pyspark.sql.functions import regexp_replace, col, lit, regexp_extract, round

# Define schema
election_schema = StructType([
    StructField("ac_name", StringType(), True),
    StructField("ac_no", LongType(), True),
    StructField("type", StringType(), True),
    StructField("district", StringType(), True),
    StructField("winning_cand", StringType(), True),
    StructField("party", StringType(), True),
    StructField("totelectors", StringType(), True),
    StructField("totvotes", StringType(), True),
    StructField("poll_percentage", StringType(), True),
    StructField("margin", StringType(), True),
    StructField("winning_percentage", StringType(), True)
])

df1 = spark.read.option("header", True).schema(election_schema).csv(files)

#remove records when all the columns are empty
df1 = df1.na.drop(how='all')

df1 = (
    df1.withColumn("totelectors", regexp_replace(col("totelectors"), ",", "").cast("long"))
       .withColumn("totvotes", regexp_replace(col("totvotes"), ",", "").cast("long"))
       .withColumn("margin", regexp_replace(col("margin"), ",", "").cast("long"))
       .withColumn("poll_percentage", round(regexp_replace(col("poll_percentage"), "%", "").cast("float")).cast("long"))
       .withColumn("winning_percentage", round(regexp_replace(col("winning_percentage"), "%", "").cast("float")).cast("long"))
)

# Add filename as int as the first column
df1 = df1.withColumn(
    "filename",
    regexp_extract(col("_metadata.file_name"), r"(\d{4})\.csv$", 1).cast("int")
).select("filename", *df1.columns)

display(df1)

filename ac_name ac_no type district winning_cand party totelectors totvotes poll_percentage margin winning_percentage 2011 Gummidipoondi 1 GEN Thiruvallur Sekar C H Desiya Murpokku Dravida Kazhagam 215430 178276 83 29101 16 2011 Ponneri 2 SC Thiruvallur Pon. Raja All India Anna Dravida Munnetra Kazhagam 202421 163088 81 31073 19 2011 Tiruttani 3 GEN Thiruvallur Arunsubramanian. M Desiya Murpokku Dravida Kazhagam 236718 191237 81 23930 13 2011 Thiruvallur 4 GEN Thiruvallur Ramana B.V All India Anna Dravida Munnetra Kazhagam 207922 170115 82 23648 14 2011 Poonmallae 5 SC Thiruvallur Manimaran R All India Anna Dravida Munnetra Kazhagam 229436 181531 79 41419 23 2011 Avadi 6 GEN Thiruvallur Abdul Rahim.S All India Anna Dravida Munnetra Kazhagam 277856 199538 72 43238 22 2011 Maduravoyal 7 GEN Thiruvallur Beem Rao. G Communist Party Of India (MARXIST) 269487 185925 69 24011 13 2011 Ambattur 8 GEN Thiruvallur Vedhachalam. S All India Anna Dravida Munnetra Kazhagam 264960 186347 70 22717 12 2011 Madavaram 9 GEN Thiruvallur Moorthy V All India Anna Dravida Munnetra Kazhagam 275590 207325 75 34765 17 2011 Thiruvottiyur 10 GEN Thiruvallur Kuppan, K. All India Anna Dravida Munnetra Kazhagam 221456 164716 74 27291 17 2011 Dr.Radhakrishnan Nagar 11 GEN Chennai Vetriivel P All India Anna Dravida Munnetra Kazhagam 195146 141942 73 31255 22 2011 Perambur 12 GEN Chennai Soundararajan A Communist Party Of India (MARXIST) 232333 162026 70 17423 11 2011 Kolathur 13 GEN Chennai Stalin M.K. Dravida Munetra Kazhagam 207990 141989 68 2819 2 2011 Villivakkam 14 GEN Chennai Prabhakar Jcd All India Anna Dravida Munnetra Kazhagam 193208 130828 68 10782 8 2011 Thiru-Vi-Ka-Nagar 15 SC Chennai Neelakandan. V All India Anna Dravida Munnetra Kazhagam 181235 123807 68 29341 24 2011 Egmore 16 SC Chennai Nallathambi K Desiya Murpokku Dravida Kazhagam 164759 111996 68 202 0 2011 Royapuram 17 GEN Chennai Jayakumar. D All India Anna Dravida Munnetra Kazhagam 159335 112461 71 21372 19 2011 Harbour 18 GEN Chennai Karuppiah .Pala All India Anna Dravida Munnetra Kazhagam 152784 96475 63 20317 21 2011 Chepauk-Thiruvallikeni 19 GEN Chennai Anbazhagan. J Dravida Munetra Kazhagam 187297 129836 69 9203 7 2011 Thousand Lights 20 GEN Chennai Valarmathi. B All India Anna Dravida Munnetra Kazhagam 199978 133567 67 7592 6 2011 Anna Nagar 21 GEN Chennai Gokula Indira S All India Anna Dravida Munnetra Kazhagam 226816 151608 67 36590 24 2011 Virugampakkam 22 GEN Chennai Partha Sarathy B Desiya Murpokku Dravida Kazhagam 214871 144069 67 14094 10 2011 Saidapet 23 GEN Chennai Senthamizhan.G All India Anna Dravida Munnetra Kazhagam 219001 154225 70 12071 8 2011 Thiyagarayanagar 24 GEN Chennai Kalairajan V P All India Anna Dravida Munnetra Kazhagam 194890 129751 67 32462 25 2011 Mylapore 25 GEN Chennai Rajalakshmi R All India Anna Dravida Munnetra Kazhagam 215336 142882 66 29204 20 2011 Velachery 26 GEN Chennai Ashok M.K. All India Anna Dravida Munnetra Kazhagam 227204 152364 67 31720 21 2011 Shozhinganallur 27 GEN Kancheepuram K.P. Kandan All India Anna Dravida Munnetra Kazhagam 357640 240583 67 66972 28 2011 Alandur 28 GEN Kancheepuram S. Ramachandran Desiya Murpokku Dravida Kazhagam 239936 168135 70 5754 3 2011 Sriperumbudur 29 SC Kancheepuram R. Perumal All India Anna Dravida Munnetra Kazhagam 210438 172263 82 40932 24 2011 Pallavaram 30 GEN Kancheepuram P. Dhansingh All India Anna Dravida Munnetra Kazhagam 277644 200455 72 17374 9 2011 Tambaram 31 GEN Kancheepuram T. K. M. Chinneyah All India Anna Dravida Munnetra Kazhagam 254995 178230 70 13984 8 2011 Chengalpattu 32 GEN Kancheepuram D. Murugesan Desiya Murpokku Dravida Kazhagam 252356 186867 74 291 0 2011 Thiruporur 33 GEN Kancheepuram K. Manoharan All India Anna Dravida Munnetra Kazhagam 192000 158639 83 18288 12 2011 Cheyyur 34 SC Kancheepuram V. S . Raji All India Anna Dravida Munnetra Kazhagam 173908 140871 81 26584 19 2011 Madurantakam 35 SC Kancheepuram S. Kanitha All India Anna Dravida Munnetra Kazhagam 180482 147744 82 1

In [0]:
df.write.mode("overwrite").parquet("/mnt/elections_curated/elections/")
df1.write.mode("append").parquet("/mnt/elections_curated/elections/")

In [0]:
df_new = spark.read.parquet("/mnt/elections_curated/elections/")
display(df_new)

filename ac_name ac_no type district winning_cand party totelectors totvotes poll_percentage margin winning_percentage 1977 Royapuram 1 GEN null P. Ponnurangam Dravida Munetra Kazhagam 141692 72868 51 1591 2 1977 Harbour 2 GEN null A. Selvarajan Dravida Munetra Kazhagam 150577 65557 44 5983 9 1977 Dr. Radhakrishnan Nagar 3 GEN null Isari Velan All India Anna Dravida Munnetra Kazhagam 178751 80748 45 1488 2 1977 Park Town 4 GEN null T.S. Nallathambi Dravida Munetra Kazhagam 145578 69199 48 3226 5 1977 Perambur 5 SC null S. Balan Dravida Munetra Kazhagam 184688 80705 44 13468 17 1977 Purasawalkam 6 GEN null K. Anbazhagan Dravida Munetra Kazhagam 203098 91943 45 19069 21 1977 Egmore 7 SC null S.Manimudi Dravida Munetra Kazhagam 141812 69887 49 7332 11 1977 Anna Nagar 8 GEN null M. Karunanidhi Dravida Munetra Kazhagam 178266 86717 49 16438 19 1977 Theagaraya Nagar 9 GEN null R.E. Chandran Jayapal Dravida Munetra Kazhagam 180871 76185 42 1030 1 1977 Thousand Lights 10 GEN null S.J. Sadiq Pasha Dravida Munetra Kazhagam 167463 72284 43 4858 7 1977 Chepauk 11 GEN null A. Rahaman Khan Dravida Munetra Kazhagam 123253 64140 52 6629 10 1977 Triplicane 12 GEN null M. Aranganathan Dravida Munetra Kazhagam 132743 66440 50 2127 3 1977 Mylapore 13 GEN null T.K. Kapali Dravida Munetra Kazhagam 152323 77911 51 4906 6 1977 Saidapet 14 GEN null D. Purushothaman Dravida Munetra Kazhagam 148319 74578 50 5278 7 1977 Gummidipundi 15 GEN null S. Munirathinam All India Anna Dravida Munnetra Kazhagam 121875 77810 64 11267 15 1977 Ponneri 16 SC null S.M. Dorairaj All India Anna Dravida Munnetra Kazhagam 134125 75794 57 11272 15 1977 Thiruvottiyur 17 GEN null P. Sigamony All India Anna Dravida Munnetra Kazhagam 148299 85676 58 2463 3 1977 Villivakkam 18 GEN null K. Suppu Dravida Munetra Kazhagam 165872 92190 56 7898 9 1977 Alandur 19 GEN null Abdul Razack All India Anna Dravida Munnetra Kazhagam 154152 83605 54 3849 5 1977 Tambaram 20 GEN null Munu Adhi All India Anna Dravida Munnetra Kazhagam 157010 93097 59 426 1 1977 Tirupporur 21 SC null G. Chokkalingam Dravida Munetra Kazhagam 97060 56642 58 2101 4 1977 Chengalpattu 22 GEN null Jagadeesan Anoor All India Anna Dravida Munnetra Kazhagam 110575 68431 62 3870 6 1977 Maduranthakam 23 GEN null C. Arumugam Dravida Munetra Kazhagam 104339 75967 73 7332 10 1977 Acharapakkam 24 SC null Ethraj All India Anna Dravida Munnetra Kazhagam 98677 63099 64 2797 4 1977 Uthiramerur 25 GEN null S. Pakkur Subramanyan All India Anna Dravida Munnetra Kazhagam 116733 78553 67 12583 16 1977 Kancheepuram 26 GEN null K. Balaji All India Anna Dravida Munnetra Kazhagam 123336 89309 72 1947 2 1977 Sriperumbudur 27 SC null N. Krishnan All India Anna Dravida Munnetra Kazhagam 108219 68838 64 8137 12 1977 Poonamallee 28 GEN null D. Irajarathanam Dravida Munetra Kazhagam 143250 74148 52 4893 7 1977 Tiruvallur 29 GEN null S. Pattabiraman All India Anna Dravida Munnetra Kazhagam 109003 68704 63 8302 12 1977 Tiruttani 30 GEN null R. Shanmugham All India Anna Dravida Munnetra Kazhagam 102979 67645 66 10316 15 1977 Pallipet 31 GEN null Enkambara Reddy Indian National Congress 110571 70972 64 4286 6 1977 Arkonam 32 SC null V.K. Raju All India Anna Dravida Munnetra Kazhagam 119208 74384 62 7589 10 1977 Sholinghur 33 GEN null S.J. Ramaswamy All India Anna Dravida Munnetra Kazhagam 112141 68973 62 5649 8 1977 Ranipet 34 GEN null Duraimurugan Dravida Munetra Kazhagam 118555 74645 63 15297 21 1977 Arcot 35 GEN null K.J. Uyyakondan All India Anna Dravida Munnetra Kazhagam 108773 70141 65 10579 15 1977 Katpadi 36 GEN null M.A. Jayavelu All India Anna Dravida Munnetra Kazhagam 113689 71307 63 4690 7 1977 Gudiyatham 37 GEN null V.K. Kothandaraman Communist Party Of India (MARXIST) 106905 70693 66 2544 4 1977 Pernambut 38 SC null I. Tamilarsan All India Anna Dravida Munnetra Kazhagam 103535 67013 65 3663 6 1977 Vaniayambadi 39 GEN null M. Abdul Latheef Independent 109540 62983 58 8734 14 1977 Natrampalli 40 GEN null T. Ambazhagan All India Anna Dravida

**Cleaning the Bronze data using SQL**

In [0]:
%sql
--CREATE DATABASE TNElection;
SHOW DATABASES;


databaseName default tnelection

In [0]:
%sql
use tnelection;
show tables;

database tableName isTemporary _sqldf true results true

In [0]:
df_new.write.format("delta").mode("overwrite").saveAsTable("tnelection.results")

In [0]:
%sql SHOW TABLE EXTENDED FROM tnelection LIKE 'results'

database tableName isTemporary information tnelection results false Catalog: spark_catalog
Database: tnelection
Table: results
Owner: root
Created Time: Wed Dec 10 03:07:13 UTC 2025
Last Access: UNKNOWN
Created By: Spark 4.0.0
Type: MANAGED
Provider: delta
Table Properties: [delta.enableDeletionVectors=true]
Location: dbfs:/user/hive/warehouse/tnelection.db/results
Serde Library: org.apache.hadoop.hive.serde2.lazy.LazySimpleSerDe
InputFormat: org.apache.hadoop.mapred.SequenceFileInputFormat
OutputFormat: org.apache.hadoop.hive.ql.io.HiveSequenceFileOutputFormat
Partition Provider: Catalog
Schema: root
 |-- filename: integer (nullable = true)
 |-- ac_name: string (nullable = true)
 |-- ac_no: long (nullable = true)
 |-- type: string (nullable = true)
 |-- district: string (nullable = true)
 |-- winning_cand: string (nullable = true)
 |-- party: string (nullable = true)
 |-- totelectors: long (nullable = true)
 |-- totvotes: long (nullable = true)
 |-- poll_percentage: long (nullable = true)
 |-- margin: long (nullable = true)
 |-- winning_percentage: long (nullable = true)

 results true Table: results
Created Time: Wed Dec 10 02:39:35 UTC 2025
Last Access: UNKNOWN
Created By: Spark 
Type: VIEW
View Schema Mode: BINDING
Schema: root
 |-- filename: integer (nullable = true)
 |-- ac_name: string (nullable = true)
 |-- ac_no: long (nullable = true)
 |-- type: string (nullable = true)
 |-- district: string (nullable = true)
 |-- winning_cand: string (nullable = true)
 |-- party: string (nullable = true)
 |-- totelectors: long (nullable = true)
 |-- totvotes: long (nullable = true)
 |-- poll_percentage: long (nullable = true)
 |-- margin: long (nullable = true)
 |-- winning_percentage: long (nullable = true)

In [0]:
%sql
UPDATE tnelection.results
SET party = 'Communist Party Of India'
WHERE party = 'CPI'

num_affected_rows 8

In [0]:
%sql
UPDATE tnelection.results
SET party = 'All India Forward Bloc'
WHERE party = 'AIFB'

num_affected_rows 7

In [0]:
%sql
UPDATE tnelection.results
SET party = 'Communist Party Of India (MARXIST)'
WHERE party = 'Communist Party Of India (Marxist)';

UPDATE tnelection.results
SET party = 'Dravida Munetra Kazhagam'
WHERE party = 'DMK';

UPDATE tnelection.results
SET party = 'Indian National Congress'
WHERE party = 'INC';

UPDATE tnelection.results
SET party = 'Indian Union Muslim League'
WHERE party = 'IUML';

UPDATE tnelection.results
SET party = 'Janata Party (JP)'
WHERE party = 'Janta Party';

num_affected_rows 17

In [0]:
%sql
select distinct party from tnelection.results

party Thayaga Marumalrchi Kazhagam All India Forward Bloc Ambedkar Kranti Dal Jharkhand Party Pattali Makkal Katchi Indian National Congress Gandhi Kamraj National Congress Puthiya Tamilagam PSP M.G.R.Anna D.M.Kazhagam Janata Party (JP) Indian National Congress (I) All India Anna Dravida Munnetra Kazhagam(JAYALALITA GROUP) Bharatiya Janta Party Communist Party Of India (MARXIST) SWA Dravida Munetra Kazhagam Viduthalai Chiruthaigal Katchi Communist Party Of India Janata Dal Tamil Maanila Congress (MOOPANAR) Indian Union Muslim League Manithaneya Makkal Katchi All India Anna Dravida Munnetra Kazhagam All India Anna Dravida Munnetra Kazhagam(JANAKI RAMACHANDRAN) Marumalarchi Dravida Munnetra Kazhagam Indian Congress (SOCIALIST- SARAT CHANDRA SINHA) Desiya Murpokku Dravida Kazhagam Independent

In [0]:
%sql
select filename as year, ac_name, ac_no, type, district, winning_cand, party, totelectors, totvotes, poll_percentage,
margin, winning_percentage
from tnelection.results
where type is null
order by filename
--limit 10

year ac_name ac_no type district winning_cand party totelectors totvotes poll_percentage margin winning_percentage 1971 Srivilliputhur 207 null null K. Gurusamy Alias Andi Dravida Munetra Kazhagam 65554 41522 63 24032 37 1971 Aravakurichi 147 null null Abdul Jabbar Indian Union Muslim League 56845 34164 60 22681 40 1971 Tirukkoyilur 66 null null A. S. Kumarasamy Dravida Munetra Kazhagam 69694 38520 55 31174 45 1971 Yercaud 85 null null Chinnusamy V. Dravida Munetra Kazhagam 48012 29196 61 18816 39 1971 Kumbakonam 173 null null N. Kasiraman Indian National Congress 77269 39755 51 37514 49 1971 Killiyoor 234 null null N. Dennis Indian National Congress 55539 34573 62 20966 38 1971 Panruti 58 null null S. Ramachandaran Dravida Munetra Kazhagam 80947 42141 52 38806 48 1971 Mugaiyur 67 null null A. G. Padmavathi Dravida Munetra Kazhagam 64595 38744 60 25851 40 1971 Dharmapuri 77 null null R. Chinnasamy Dravida Munetra Kazhagam 73599 39861 54 33738 46 1971 Panamrathupatti 86 null null Karipatti T. Ponnumalai Dravida Munetra Kazhagam 65843 35832 54 30011 46 1971 Rasipuram 94 null null R. Nainamalai Dravida Munetra Kazhagam 74825 41079 55 33746 45 1971 Kadavur 164 null null Karuraigiri Muthiah Indian National Congress 61511 31752 52 29759 48 1971 Padmanabhapuram 231 null null A. Swamidhas Indian National Congress 57834 32416 56 25418 44 1971 Gingee 51 null null S. Sagadeva Gounder Dravida Munetra Kazhagam 66025 39397 60 26628 40 1971 Tirumangalam 133 null null M. C. A. Rethinasamy Thevar All India Forward Bloc 64013 36468 57 27545 43 1971 Triplicane 9 null null V. R. Nedunchezhiyan Dravida Munetra Kazhagam 71899 36237 50 35662 50 1971 Washermanpet 1 null null M. Vedachalam Dravida Munetra Kazhagam 72148 38989 54 33159 46 1971 Kunnathur 23 null null M. Gopal Dravida Munetra Kazhagam 73086 47126 64 25960 36 1971 Perambur 5 null null Sathyavani Muthu Dravida Munetra Kazhagam 87050 49070 56 37980 44 1971 Tiruttani 27 null null E. S. Thyagarajan Dravida Munetra Kazhagam 70376 43436 62 26940 38 1971 Egmore 7 null null Arangannal Dravida Munetra Kazhagam 76323 40596 53 35727 47 1971 Gudiyatham 33 null null Duraisami F. K. Dravida Munetra Kazhagam 61997 34954 56 27043 44 1971 Sattur 205 null null S. Alagu Thevar All India Forward Bloc 58831 32610 55 26221 45 1971 Maduranthakam 19 null null C. Arumugam Dravida Munetra Kazhagam 65543 42295 65 23248 35 1971 Gummidipoondi 13 null null K. A. Vezhavendan Dravida Munetra Kazhagam 74225 43355 58 30870 42 1971 Vilavancode 233 null null R. Ponnappan Nadar Indian National Congress 52013 32139 62 19874 38 1971 Pudukkottai 168 null null M. Sathiamoorthy Indian National Congress 74103 34680 47 39423 53 1971 Dindigul 144 null null Sundaram Pillai O. N. Indian National Congress 69786 27775 40 42011 60 1971 Kariapatti 202 null null Perumal A. R. All India Forward Bloc 61366 31499 51 29867 49 1971 St Thomas Mount 16 null null M. G. Ramachandran Dravida Munetra Kazhagam 107028 65405 61 41623 39 1971 Vilathikulam 209 null null M. Rathnasabapathy Dravida Munetra Kazhagam 56834 32583 57 24251 43 1971 Kattumannarkoil 61 null null S. Perumal Dravida Munetra Kazhagam 63509 32847 52 30662 48 1971 Nilakottai 135 null null A. Muniyandi Dravida Munetra Kazhagam 63127 38583 61 24544 39 1971 Madurai East 140 null null K. Ramakrishnan K. S. Dravida Munetra Kazhagam 63186 27884 44 35302 56 1971 Athoor 145 null null A. M. T. Nachiappan Dravida Munetra Kazhagam 70678 42195 60 28483 40 1971 Sankarapuram 69 null null N. Natchiyappan Dravida Munetra Kazhagam 57020 28544 50 28476 50 1971 Andimadam 154 null null S. Sadasiva Padayachi Dravida Munetra Kazhagam 74106 39313 53 34793 47 1971 Tiruchirappalli I 159 null null V. Krishnamurthy Dravida Munetra Kazhagam 72363 38099 53 34264 47 1971 Krishnarayapuram 163 null null P. Soundarapandiyan Dravida Munetra Kazhagam 65741 36177 55 29564 45 1971 Pennagaram 79 null null N. Manickkam Dravida Munetra Kazhagam 63594 33298 52 30296 48 1971 Aduthurai 174 null null K. Rajamanickam Dravida Mune

**Mounting Silver container**

In [0]:
dbutils.fs.mount(
  source = "wasbs://analytics@tnelectionanalytics.blob.core.windows.net/",
  mount_point = "/mnt/elections_silver",
  extra_configs = configs
)

True

In [0]:
df_byelection = spark.read.csv("/mnt/elections_raw/elections/TN Bye-Elections .csv", header=True, inferSchema=True)


In [0]:
display(df_byelection)

AC Name AC No Type State Winning Party Electors Votes turnout Reason year Panamarathupatty 91 NA Tamil Nadu K.Rajaram ADK NA NA NA DEATH OF SHRI N.SUBBARAYAN 1977 Usilampatti 138 NA Tamil Nadu A.Thevar.S FBL NA NA NA DEATH OF SHRI P.K.M.THAVER 1977 Vilavancode 233 NA Tamil Nadu Packiadas.D CPM NA NA NA DEATH OF SHRI D.GNANASIGAMONY 1977 Anna 8 NA Tamil Nadu Eramachandran.S.M DMK NA NA NA RESIGNATION OF Dr. M.KARUNANIDHI 1980 Mayuram 171 NA Tamil Nadu Sathiyaseelan.K DMK NA NA NA DEATH OF SHRI N.KITTAPPA 1980 Thanjavur 183 NA Tamil Nadu A.Vandayar.K INC NA NA NA DEATH OF SHRI N.NATARAJAN 1980 Tiruppattur 194 NA Tamil Nadu Arunagiri.R INC(I) NA NA NA DEATH OF SHRI V.VALMIGI 1980 Uppiliapuram 157 ST Tamil Nadu Saroja.R.(W) ADK NA NA NA VOID OF SHRI V.ARENGARAN ELECTION. 1980 Aruppukottai 204 NA Tamil Nadu V.S.Panchavarnam ADK NA NA NA DEATH OF SHRI M.PITCHAI 1984 Cheyyar 50 NA Tamil Nadu V.Kuppusamy ADK NA NA NA DEATH OF SHRI K.MURUGAN 1984 Tirunelveli 218 NA Tamil Nadu Veerappan.R.M ADK NA NA NA DEATH OF SHRI S.NARAYANAN 1984 Tiruppattur 41 NA Tamil Nadu Manavalan,s.P INC NA NA NA DEATH OF SHRI Y.SHANMUGAM 1984 Harbour 2 NA Tamil Nadu Selvarasam DMK NA NA NA RESIGNATION OF SHRI M.KARUNIDHI 1991 Kangayam 117 NA Tamil Nadu E.Veerappan ADK NA NA NA RESIGNATION OF MS.J.JAYALALITHA 1991 Aruppukottai 204 GEN Tamil Nadu Thangamthenarasu DMK 1,67,272 1,10,183 65.90% NA 1996 Coonoor 126 SC Tamil Nadu Ranganathan M DMK 1,69,753 99,348 58.50% NA 1996 Natham 147 GEN Tamil Nadu Viswanathan.R ADMK 1,82,655 1,13,236 NA NA 1996 Nellikppam 62 GEN Tamil Nadu Shanmugam V.C. DMK 1,71,250 1,12,123 65.50% Death - Sh. A. Mani 1996 Pudukkottai 191 GEN Tamil Nadu Mari Ayya P. DMK 2,16,230 1,44,523 66.80% NA 1996 Tiruchirapalli 167 GEN Tamil Nadu Anbil Periyasamy DMK 2,21,587 1,05,338 47.50% Death - Sh.Anbil Poyyamozhi 1996 Acharapakam 24 GEN Tamil Nadu A.Bhuvaraghamoorthy AIADMK 1,67,240 1,03,911 62.10% Death of Shri A.Selvaraj 2001 Andipatti 135 GEN Tamil Nadu Jayalalithaa J. AIADMK 2,08,576 1,34,744 64.60% Resignation of Thiru Thanga Tamilselvan 2001 Gummidipundi 15 GEN Tamil Nadu Vijayakumar Ks AIADMK 1,93,346 1,47,032 76% Due to death of Shri Thiru Sudarsanam. 2001 Kancheepuram 26 GEN Tamil Nadu Mythili (TMT) AIADMK 2,35,636 1,64,443 69.80% Due to death of Shri Thiru S.S.Thirunavukkarasu. 2001 Mangalore 70 GEN Tamil Nadu Ganesan V. DMK 2,08,405 1,42,080 68.20% Resignation of Shri Thirumavalavan 2001 Saidapet 14 GEN Tamil Nadu Radha Ravi ADMK 2,48,003 1,29,433 52.20% Death of Shri V.Perumal 2001 Sattangulam 224 GEN Tamil Nadu Neelamegavarnam L. ADMK 1,55,093 1,00,447 64.80% Death of Shri S.S. Mani Nadar 2001 Viniyambadi 39 GEN Tamil Nadu Vadivel. R AIADMK 2,02,883 1,29,217 63.70% Death of Shri M.Abdul Latheef 2001 Madurai Central 143 GEN Tamil Nadu Syed Ghouse Basha, S. DMK 1,32,358 90,897 68.70% Due to the death of Thiru P.T.R. Palanivel Rajan formerly member of this assembly constituency, this assembly seat has been declared vacant. 2006 Madurai West 142 GEN Tamil Nadu Rajendren, K.S.K INC 1,56,454 1,17,910 75.40% Due todeath of Shri S.V.Shanmugam 2006 Alandur 28 GEN Tamil Nadu Venkatraman V.N.P. All India Anna Dravida Munnetra Kazhagam 2,39,936 2,01,216 83.90% NA 2011 Pudukkottai 180 GEN Tamil Nadu K. Thondaiman AIADMK 1,95,049 1,43,346 73.50% Due to Death 2011 Sankarankouil 219 SC Tamil Nadu Muthu Selvi .S AIADK 2,06,465 1,59,772 77.40% Due to death 2011 Tiruchirappalli (West) 140 GEN Tamil Nadu Paranjothi M. AIDMK 2,08,491 1,27,433 61.10% Due to Death 2011

In [0]:
# Rename columns to clean, snake_case names
df_clean = (
    df_byelection
    .withColumnRenamed("AC Name", "ac_name")
    .withColumnRenamed("AC No", "ac_no")
    .withColumnRenamed("Type", "type")
    .withColumnRenamed("State", "state")
    .withColumnRenamed("Winning", "winning_cand")
    .withColumnRenamed("Party ", "party")   # removed trailing space
    .withColumnRenamed("Electors", "totelectors")
    .withColumnRenamed("Votes", "totvotes")
    .withColumnRenamed("turnout", "poll_percentage")
    .withColumnRenamed("Reason", "reason")
    .withColumnRenamed("year", "year")
)

# Save as Delta table
df_clean.write.format("delta").mode("overwrite").saveAsTable("tnelection.by_election")

In [0]:
%sql
select * from tnelection.by_election


ac_name ac_no type state winning_cand party totelectors totvotes poll_percentage reason year Panamarathupatty 91 NA Tamil Nadu K.Rajaram ADK NA NA NA DEATH OF SHRI N.SUBBARAYAN 1977 Usilampatti 138 NA Tamil Nadu A.Thevar.S FBL NA NA NA DEATH OF SHRI P.K.M.THAVER 1977 Vilavancode 233 NA Tamil Nadu Packiadas.D CPM NA NA NA DEATH OF SHRI D.GNANASIGAMONY 1977 Anna 8 NA Tamil Nadu Eramachandran.S.M DMK NA NA NA RESIGNATION OF Dr. M.KARUNANIDHI 1980 Mayuram 171 NA Tamil Nadu Sathiyaseelan.K DMK NA NA NA DEATH OF SHRI N.KITTAPPA 1980 Thanjavur 183 NA Tamil Nadu A.Vandayar.K INC NA NA NA DEATH OF SHRI N.NATARAJAN 1980 Tiruppattur 194 NA Tamil Nadu Arunagiri.R INC(I) NA NA NA DEATH OF SHRI V.VALMIGI 1980 Uppiliapuram 157 ST Tamil Nadu Saroja.R.(W) ADK NA NA NA VOID OF SHRI V.ARENGARAN ELECTION. 1980 Aruppukottai 204 NA Tamil Nadu V.S.Panchavarnam ADK NA NA NA DEATH OF SHRI M.PITCHAI 1984 Cheyyar 50 NA Tamil Nadu V.Kuppusamy ADK NA NA NA DEATH OF SHRI K.MURUGAN 1984 Tirunelveli 218 NA Tamil Nadu Veerappan.R.M ADK NA NA NA DEATH OF SHRI S.NARAYANAN 1984 Tiruppattur 41 NA Tamil Nadu Manavalan,s.P INC NA NA NA DEATH OF SHRI Y.SHANMUGAM 1984 Harbour 2 NA Tamil Nadu Selvarasam DMK NA NA NA RESIGNATION OF SHRI M.KARUNIDHI 1991 Kangayam 117 NA Tamil Nadu E.Veerappan ADK NA NA NA RESIGNATION OF MS.J.JAYALALITHA 1991 Aruppukottai 204 GEN Tamil Nadu Thangamthenarasu DMK 1,67,272 1,10,183 65.90% NA 1996 Coonoor 126 SC Tamil Nadu Ranganathan M DMK 1,69,753 99,348 58.50% NA 1996 Natham 147 GEN Tamil Nadu Viswanathan.R ADMK 1,82,655 1,13,236 NA NA 1996 Nellikppam 62 GEN Tamil Nadu Shanmugam V.C. DMK 1,71,250 1,12,123 65.50% Death - Sh. A. Mani 1996 Pudukkottai 191 GEN Tamil Nadu Mari Ayya P. DMK 2,16,230 1,44,523 66.80% NA 1996 Tiruchirapalli 167 GEN Tamil Nadu Anbil Periyasamy DMK 2,21,587 1,05,338 47.50% Death - Sh.Anbil Poyyamozhi 1996 Acharapakam 24 GEN Tamil Nadu A.Bhuvaraghamoorthy AIADMK 1,67,240 1,03,911 62.10% Death of Shri A.Selvaraj 2001 Andipatti 135 GEN Tamil Nadu Jayalalithaa J. AIADMK 2,08,576 1,34,744 64.60% Resignation of Thiru Thanga Tamilselvan 2001 Gummidipundi 15 GEN Tamil Nadu Vijayakumar Ks AIADMK 1,93,346 1,47,032 76% Due to death of Shri Thiru Sudarsanam. 2001 Kancheepuram 26 GEN Tamil Nadu Mythili (TMT) AIADMK 2,35,636 1,64,443 69.80% Due to death of Shri Thiru S.S.Thirunavukkarasu. 2001 Mangalore 70 GEN Tamil Nadu Ganesan V. DMK 2,08,405 1,42,080 68.20% Resignation of Shri Thirumavalavan 2001 Saidapet 14 GEN Tamil Nadu Radha Ravi ADMK 2,48,003 1,29,433 52.20% Death of Shri V.Perumal 2001 Sattangulam 224 GEN Tamil Nadu Neelamegavarnam L. ADMK 1,55,093 1,00,447 64.80% Death of Shri S.S. Mani Nadar 2001 Viniyambadi 39 GEN Tamil Nadu Vadivel. R AIADMK 2,02,883 1,29,217 63.70% Death of Shri M.Abdul Latheef 2001 Madurai Central 143 GEN Tamil Nadu Syed Ghouse Basha, S. DMK 1,32,358 90,897 68.70% Due to the death of Thiru P.T.R. Palanivel Rajan formerly member of this assembly constituency, this assembly seat has been declared vacant. 2006 Madurai West 142 GEN Tamil Nadu Rajendren, K.S.K INC 1,56,454 1,17,910 75.40% Due todeath of Shri S.V.Shanmugam 2006 Alandur 28 GEN Tamil Nadu Venkatraman V.N.P. All India Anna Dravida Munnetra Kazhagam 2,39,936 2,01,216 83.90% NA 2011 Pudukkottai 180 GEN Tamil Nadu K. Thondaiman AIADMK 1,95,049 1,43,346 73.50% Due to Death 2011 Sankarankouil 219 SC Tamil Nadu Muthu Selvi .S AIADK 2,06,465 1,59,772 77.40% Due to death 2011 Tiruchirappalli (West) 140 GEN Tamil Nadu Paranjothi M. AIDMK 2,08,491 1,27,433 61.10% Due to Death 2011

In [0]:
%sql
-- SQL Script to Standardize Party Names in by_election table

-- 1. Communist Party of India (Marxist) (CPM)
UPDATE tnelection.by_election
SET party = 'Communist Party Of India (MARXIST)'
WHERE party = 'CPM';

-- 2. Dravida Munnetra Kazhagam (DMK)
UPDATE tnelection.by_election
SET party = 'Dravida Munetra Kazhagam'
WHERE party = 'DMK';

-- 3. Indian National Congress (INC and INC(I))
UPDATE tnelection.by_election
SET party = 'Indian National Congress'
WHERE party = 'INC';

UPDATE tnelection.by_election
SET party = 'Indian National Congress (I)'
WHERE party = 'INC(I)';

-- 4. All India Anna Dravida Munnetra Kazhagam (Various forms)
UPDATE tnelection.by_election
SET party = 'All India Anna Dravida Munnetra Kazhagam'
WHERE party IN ('ADMK', 'AIADMK', 'AIADK', 'AIDMK');

-- Standardize NA values to NULL
UPDATE tnelection.by_election
SET type = NULL
WHERE type = 'NA';

UPDATE tnelection.by_election
SET totelectors = NULL
WHERE totelectors = 'NA';

UPDATE tnelection.by_election
SET totvotes = NULL
WHERE totvotes = 'NA';

UPDATE tnelection.by_election
SET poll_percentage = NULL
WHERE poll_percentage = 'NA';

num_affected_rows 15

In [0]:
%sql
select * from tnelection.by_election


ac_name ac_no type state winning_cand party totelectors totvotes poll_percentage reason year Uppiliapuram 157 By election Tamil Nadu Saroja.R.(W) ADK null null null VOID OF SHRI V.ARENGARAN ELECTION. 1980 Natham 147 By election Tamil Nadu Viswanathan.R All India Anna Dravida Munnetra Kazhagam 182655 113236 null NA 1996 Tiruppattur 194 By election Tamil Nadu Arunagiri.R Indian National Congress (I) null null null DEATH OF SHRI V.VALMIGI 1980 Thanjavur 183 By election Tamil Nadu A.Vandayar.K Indian National Congress null null null DEATH OF SHRI N.NATARAJAN 1980 Tiruppattur 41 By election Tamil Nadu Manavalan,s.P Indian National Congress null null null DEATH OF SHRI Y.SHANMUGAM 1984 Vilavancode 233 By election Tamil Nadu Packiadas.D Communist Party Of India (MARXIST) null null null DEATH OF SHRI D.GNANASIGAMONY 1977 Anna 8 By election Tamil Nadu Eramachandran.S.M Dravida Munetra Kazhagam null null null RESIGNATION OF Dr. M.KARUNANIDHI 1980 Mayuram 171 By election Tamil Nadu Sathiyaseelan.K Dravida Munetra Kazhagam null null null DEATH OF SHRI N.KITTAPPA 1980 Harbour 2 By election Tamil Nadu Selvarasam Dravida Munetra Kazhagam null null null RESIGNATION OF SHRI M.KARUNIDHI 1991 Panamarathupatty 91 By election Tamil Nadu K.Rajaram ADK null null null DEATH OF SHRI N.SUBBARAYAN 1977 Usilampatti 138 By election Tamil Nadu A.Thevar.S FBL null null null DEATH OF SHRI P.K.M.THAVER 1977 Aruppukottai 204 By election Tamil Nadu V.S.Panchavarnam ADK null null null DEATH OF SHRI M.PITCHAI 1984 Cheyyar 50 By election Tamil Nadu V.Kuppusamy ADK null null null DEATH OF SHRI K.MURUGAN 1984 Tirunelveli 218 By election Tamil Nadu Veerappan.R.M ADK null null null DEATH OF SHRI S.NARAYANAN 1984 Kangayam 117 By election Tamil Nadu E.Veerappan ADK null null null RESIGNATION OF MS.J.JAYALALITHA 1991 Acharapakam 24 By election Tamil Nadu A.Bhuvaraghamoorthy All India Anna Dravida Munnetra Kazhagam 167240 103911 62 Death of Shri A.Selvaraj 2001 Andipatti 135 By election Tamil Nadu Jayalalithaa J. All India Anna Dravida Munnetra Kazhagam 208576 134744 64 Resignation of Thiru Thanga Tamilselvan 2001 Gummidipundi 15 By election Tamil Nadu Vijayakumar Ks All India Anna Dravida Munnetra Kazhagam 193346 147032 76 Due to death of Shri Thiru Sudarsanam. 2001 Kancheepuram 26 By election Tamil Nadu Mythili (TMT) All India Anna Dravida Munnetra Kazhagam 235636 164443 69 Due to death of Shri Thiru S.S.Thirunavukkarasu. 2001 Saidapet 14 By election Tamil Nadu Radha Ravi All India Anna Dravida Munnetra Kazhagam 248003 129433 52 Death of Shri V.Perumal 2001 Sattangulam 224 By election Tamil Nadu Neelamegavarnam L. All India Anna Dravida Munnetra Kazhagam 155093 100447 64 Death of Shri S.S. Mani Nadar 2001 Viniyambadi 39 By election Tamil Nadu Vadivel. R All India Anna Dravida Munnetra Kazhagam 202883 129217 63 Death of Shri M.Abdul Latheef 2001 Pudukkottai 180 By election Tamil Nadu K. Thondaiman All India Anna Dravida Munnetra Kazhagam 195049 143346 73 Due to Death 2011 Sankarankouil 219 By election Tamil Nadu Muthu Selvi .S All India Anna Dravida Munnetra Kazhagam 206465 159772 77 Due to death 2011 Tiruchirappalli (West) 140 By election Tamil Nadu Paranjothi M. All India Anna Dravida Munnetra Kazhagam 208491 127433 61 Due to Death 2011 Madurai West 142 By election Tamil Nadu Rajendren, K.S.K Indian National Congress 156454 117910 75 Due todeath of Shri S.V.Shanmugam 2006 Aruppukottai 204 By election Tamil Nadu Thangamthenarasu Dravida Munetra Kazhagam 167272 110183 65 NA 1996 Coonoor 126 By election Tamil Nadu Ranganathan M Dravida Munetra Kazhagam 169753 99348 58 NA 1996 Nellikppam 62 By election Tamil Nadu Shanmugam V.C. Dravida Munetra Kazhagam 171250 112123 65 Death - Sh. A. Mani 1996 Pudukkottai 191 By election Tamil Nadu Mari Ayya P. Dravida Munetra Kazhagam 216230 144523 66 NA 1996 Tiruchirapalli 167 By election Tamil Nadu Anbil Periyasamy Dravida Munetra Kazhagam 221587 105338 47 Death - Sh.Anbil Poyyamozhi 1996 Mangalore 70 By election Tamil Nadu Ganesan V. D

In [0]:
%sql
-- Remove commas and cast to BIGINT
UPDATE tnelection.by_election
SET totelectors = CAST(regexp_replace(totelectors, ',', '') AS BIGINT);

UPDATE tnelection.by_election
SET totvotes = CAST(regexp_replace(totvotes, ',', '') AS BIGINT);

-- Remove % and cast to BIGINT
UPDATE tnelection.by_election
SET poll_percentage = CAST(
    CAST(regexp_replace(poll_percentage, '%', '') AS DOUBLE) AS BIGINT
);

num_affected_rows 34

In [0]:
%sql
select * from tnelection.by_election

ac_name ac_no type state winning_cand party totelectors totvotes poll_percentage reason year Uppiliapuram 157 By election Tamil Nadu Saroja.R.(W) ADK null null null VOID OF SHRI V.ARENGARAN ELECTION. 1980 Natham 147 By election Tamil Nadu Viswanathan.R All India Anna Dravida Munnetra Kazhagam 182655 113236 null NA 1996 Tiruppattur 194 By election Tamil Nadu Arunagiri.R Indian National Congress (I) null null null DEATH OF SHRI V.VALMIGI 1980 Thanjavur 183 By election Tamil Nadu A.Vandayar.K Indian National Congress null null null DEATH OF SHRI N.NATARAJAN 1980 Tiruppattur 41 By election Tamil Nadu Manavalan,s.P Indian National Congress null null null DEATH OF SHRI Y.SHANMUGAM 1984 Vilavancode 233 By election Tamil Nadu Packiadas.D Communist Party Of India (MARXIST) null null null DEATH OF SHRI D.GNANASIGAMONY 1977 Anna 8 By election Tamil Nadu Eramachandran.S.M Dravida Munetra Kazhagam null null null RESIGNATION OF Dr. M.KARUNANIDHI 1980 Mayuram 171 By election Tamil Nadu Sathiyaseelan.K Dravida Munetra Kazhagam null null null DEATH OF SHRI N.KITTAPPA 1980 Harbour 2 By election Tamil Nadu Selvarasam Dravida Munetra Kazhagam null null null RESIGNATION OF SHRI M.KARUNIDHI 1991 Panamarathupatty 91 By election Tamil Nadu K.Rajaram ADK null null null DEATH OF SHRI N.SUBBARAYAN 1977 Usilampatti 138 By election Tamil Nadu A.Thevar.S FBL null null null DEATH OF SHRI P.K.M.THAVER 1977 Aruppukottai 204 By election Tamil Nadu V.S.Panchavarnam ADK null null null DEATH OF SHRI M.PITCHAI 1984 Cheyyar 50 By election Tamil Nadu V.Kuppusamy ADK null null null DEATH OF SHRI K.MURUGAN 1984 Tirunelveli 218 By election Tamil Nadu Veerappan.R.M ADK null null null DEATH OF SHRI S.NARAYANAN 1984 Kangayam 117 By election Tamil Nadu E.Veerappan ADK null null null RESIGNATION OF MS.J.JAYALALITHA 1991 Acharapakam 24 By election Tamil Nadu A.Bhuvaraghamoorthy All India Anna Dravida Munnetra Kazhagam 167240 103911 62 Death of Shri A.Selvaraj 2001 Andipatti 135 By election Tamil Nadu Jayalalithaa J. All India Anna Dravida Munnetra Kazhagam 208576 134744 64 Resignation of Thiru Thanga Tamilselvan 2001 Gummidipundi 15 By election Tamil Nadu Vijayakumar Ks All India Anna Dravida Munnetra Kazhagam 193346 147032 76 Due to death of Shri Thiru Sudarsanam. 2001 Kancheepuram 26 By election Tamil Nadu Mythili (TMT) All India Anna Dravida Munnetra Kazhagam 235636 164443 69 Due to death of Shri Thiru S.S.Thirunavukkarasu. 2001 Saidapet 14 By election Tamil Nadu Radha Ravi All India Anna Dravida Munnetra Kazhagam 248003 129433 52 Death of Shri V.Perumal 2001 Sattangulam 224 By election Tamil Nadu Neelamegavarnam L. All India Anna Dravida Munnetra Kazhagam 155093 100447 64 Death of Shri S.S. Mani Nadar 2001 Viniyambadi 39 By election Tamil Nadu Vadivel. R All India Anna Dravida Munnetra Kazhagam 202883 129217 63 Death of Shri M.Abdul Latheef 2001 Pudukkottai 180 By election Tamil Nadu K. Thondaiman All India Anna Dravida Munnetra Kazhagam 195049 143346 73 Due to Death 2011 Sankarankouil 219 By election Tamil Nadu Muthu Selvi .S All India Anna Dravida Munnetra Kazhagam 206465 159772 77 Due to death 2011 Tiruchirappalli (West) 140 By election Tamil Nadu Paranjothi M. All India Anna Dravida Munnetra Kazhagam 208491 127433 61 Due to Death 2011 Madurai West 142 By election Tamil Nadu Rajendren, K.S.K Indian National Congress 156454 117910 75 Due todeath of Shri S.V.Shanmugam 2006 Aruppukottai 204 By election Tamil Nadu Thangamthenarasu Dravida Munetra Kazhagam 167272 110183 65 NA 1996 Coonoor 126 By election Tamil Nadu Ranganathan M Dravida Munetra Kazhagam 169753 99348 58 NA 1996 Nellikppam 62 By election Tamil Nadu Shanmugam V.C. Dravida Munetra Kazhagam 171250 112123 65 Death - Sh. A. Mani 1996 Pudukkottai 191 By election Tamil Nadu Mari Ayya P. Dravida Munetra Kazhagam 216230 144523 66 NA 1996 Tiruchirapalli 167 By election Tamil Nadu Anbil Periyasamy Dravida Munetra Kazhagam 221587 105338 47 Death - Sh.Anbil Poyyamozhi 1996 Mangalore 70 By election Tamil Nadu Ganesan V. D

In [0]:
%sql
UPDATE tnelection.by_election
SET type = 'By election'


num_affected_rows 34

In [0]:
%sql
CREATE OR REPLACE VIEW tnelection.all_elections_view AS
SELECT 
    r.filename       AS year,
    r.ac_name,
    r.ac_no,
    r.type,
    r.district,
    r.winning_cand,
    r.party,
    r.totelectors,
    r.totvotes,
    r.poll_percentage,
    r.margin,
    r.winning_percentage
FROM tnelection.results r

UNION ALL

SELECT 
    b.year           AS year,
    b.ac_name,
    b.ac_no,
    b.type,
    NULL             AS district,         -- not available in by_election
    b.winning_cand,
    b.party,
    b.totelectors,
    b.totvotes,
    b.poll_percentage,
    NULL             AS margin,           -- not available in by_election
    NULL             AS winning_percentage -- not available in by_election
FROM tnelection.by_election b;

**Final Silver data**

In [0]:
%sql

SELECT *
FROM tnelection.all_elections_view
WHERE type <> 'By election'
   OR type IS NULL;
    


year ac_name ac_no type district winning_cand party totelectors totvotes poll_percentage margin winning_percentage 2006 Perambur 5 SC null Mahendran, K. Communist Party Of India (MARXIST) 268704 182631 68 2788 2 2006 Gudiyatham 37 GEN null Latha.G Communist Party Of India (MARXIST) 178024 121384 68 1650 1 2006 Harur 79 SC null Dillibabu.P Communist Party Of India (MARXIST) 223534 155411 70 13693 9 2006 Tiruppur 116 GEN null Govindasamy.C Communist Party Of India (MARXIST) 428422 244208 57 11299 5 2006 Madurai East 144 GEN null Nanmaran.N Communist Party Of India (MARXIST) 134455 95253 71 51 0 2006 Dindigul 148 GEN null Balabarathi.K Communist Party Of India (MARXIST) 218221 152750 70 18949 12 2006 Nagapattinam 175 GEN null Marimuthu.V Communist Party Of India (MARXIST) 164819 125072 76 2344 2 2006 Thiruvattar 232 GEN null Leema Rose.R Communist Party Of India (MARXIST) 165801 110791 67 28050 25 2006 Vilavancode 233 GEN null John Joseph,g Communist Party Of India (MARXIST) 195426 120076 61 45074 38 2011 Gummidipoondi 1 GEN Thiruvallur Sekar C H Desiya Murpokku Dravida Kazhagam 215430 178276 83 29101 16 2011 Ponneri 2 SC Thiruvallur Pon. Raja All India Anna Dravida Munnetra Kazhagam 202421 163088 81 31073 19 2011 Tiruttani 3 GEN Thiruvallur Arunsubramanian. M Desiya Murpokku Dravida Kazhagam 236718 191237 81 23930 13 2011 Thiruvallur 4 GEN Thiruvallur Ramana B.V All India Anna Dravida Munnetra Kazhagam 207922 170115 82 23648 14 2011 Poonmallae 5 SC Thiruvallur Manimaran R All India Anna Dravida Munnetra Kazhagam 229436 181531 79 41419 23 2011 Avadi 6 GEN Thiruvallur Abdul Rahim.S All India Anna Dravida Munnetra Kazhagam 277856 199538 72 43238 22 2011 Maduravoyal 7 GEN Thiruvallur Beem Rao. G Communist Party Of India (MARXIST) 269487 185925 69 24011 13 2011 Ambattur 8 GEN Thiruvallur Vedhachalam. S All India Anna Dravida Munnetra Kazhagam 264960 186347 70 22717 12 2011 Madavaram 9 GEN Thiruvallur Moorthy V All India Anna Dravida Munnetra Kazhagam 275590 207325 75 34765 17 2011 Thiruvottiyur 10 GEN Thiruvallur Kuppan, K. All India Anna Dravida Munnetra Kazhagam 221456 164716 74 27291 17 2011 Dr.Radhakrishnan Nagar 11 GEN Chennai Vetriivel P All India Anna Dravida Munnetra Kazhagam 195146 141942 73 31255 22 2011 Perambur 12 GEN Chennai Soundararajan A Communist Party Of India (MARXIST) 232333 162026 70 17423 11 2011 Kolathur 13 GEN Chennai Stalin M.K. Dravida Munetra Kazhagam 207990 141989 68 2819 2 2011 Villivakkam 14 GEN Chennai Prabhakar Jcd All India Anna Dravida Munnetra Kazhagam 193208 130828 68 10782 8 2011 Thiru-Vi-Ka-Nagar 15 SC Chennai Neelakandan. V All India Anna Dravida Munnetra Kazhagam 181235 123807 68 29341 24 2011 Egmore 16 SC Chennai Nallathambi K Desiya Murpokku Dravida Kazhagam 164759 111996 68 202 0 2011 Royapuram 17 GEN Chennai Jayakumar. D All India Anna Dravida Munnetra Kazhagam 159335 112461 71 21372 19 2011 Harbour 18 GEN Chennai Karuppiah .Pala All India Anna Dravida Munnetra Kazhagam 152784 96475 63 20317 21 2011 Chepauk-Thiruvallikeni 19 GEN Chennai Anbazhagan. J Dravida Munetra Kazhagam 187297 129836 69 9203 7 2011 Thousand Lights 20 GEN Chennai Valarmathi. B All India Anna Dravida Munnetra Kazhagam 199978 133567 67 7592 6 2011 Anna Nagar 21 GEN Chennai Gokula Indira S All India Anna Dravida Munnetra Kazhagam 226816 151608 67 36590 24 2011 Virugampakkam 22 GEN Chennai Partha Sarathy B Desiya Murpokku Dravida Kazhagam 214871 144069 67 14094 10 2011 Saidapet 23 GEN Chennai Senthamizhan.G All India Anna Dravida Munnetra Kazhagam 219001 154225 70 12071 8 2011 Thiyagarayanagar 24 GEN Chennai Kalairajan V P All India Anna Dravida Munnetra Kazhagam 194890 129751 67 32462 25 2011 Mylapore 25 GEN Chennai Rajalakshmi R All India Anna Dravida Munnetra Kazhagam 215336 142882 66 29204 20 2011 Velachery 26 GEN Chennai Ashok M.K. All India Anna Dravida Munnetra Kazhagam 227204 152364 67 31720 21 2011 Shozhinganallur 27 GEN Kancheepuram K.P. Kandan All India Anna Dravida Munnetra Kazhagam 357640 240583 67 66972 28 201

In [0]:
%sql

SELECT count(*)
FROM tnelection.all_elections_view 

count(1) 2840

**Loading silver data**

In [0]:
df_all = spark.sql("SELECT * FROM tnelection.all_elections_view")
df_all.write.format("delta").mode("overwrite").save("/mnt/election_silver")

In [0]:
df_final = spark.read.load("/mnt/election_silver")
display(df_final)

year ac_name ac_no type district winning_cand party totelectors totvotes poll_percentage margin winning_percentage 2006 Perambur 5 SC null Mahendran, K. Communist Party Of India (MARXIST) 268704 182631 68 2788 2 2006 Gudiyatham 37 GEN null Latha.G Communist Party Of India (MARXIST) 178024 121384 68 1650 1 2006 Harur 79 SC null Dillibabu.P Communist Party Of India (MARXIST) 223534 155411 70 13693 9 2006 Tiruppur 116 GEN null Govindasamy.C Communist Party Of India (MARXIST) 428422 244208 57 11299 5 2006 Madurai East 144 GEN null Nanmaran.N Communist Party Of India (MARXIST) 134455 95253 71 51 0 2006 Dindigul 148 GEN null Balabarathi.K Communist Party Of India (MARXIST) 218221 152750 70 18949 12 2006 Nagapattinam 175 GEN null Marimuthu.V Communist Party Of India (MARXIST) 164819 125072 76 2344 2 2006 Thiruvattar 232 GEN null Leema Rose.R Communist Party Of India (MARXIST) 165801 110791 67 28050 25 2006 Vilavancode 233 GEN null John Joseph,g Communist Party Of India (MARXIST) 195426 120076 61 45074 38 2011 Gummidipoondi 1 GEN Thiruvallur Sekar C H Desiya Murpokku Dravida Kazhagam 215430 178276 83 29101 16 2011 Ponneri 2 SC Thiruvallur Pon. Raja All India Anna Dravida Munnetra Kazhagam 202421 163088 81 31073 19 2011 Tiruttani 3 GEN Thiruvallur Arunsubramanian. M Desiya Murpokku Dravida Kazhagam 236718 191237 81 23930 13 2011 Thiruvallur 4 GEN Thiruvallur Ramana B.V All India Anna Dravida Munnetra Kazhagam 207922 170115 82 23648 14 2011 Poonmallae 5 SC Thiruvallur Manimaran R All India Anna Dravida Munnetra Kazhagam 229436 181531 79 41419 23 2011 Avadi 6 GEN Thiruvallur Abdul Rahim.S All India Anna Dravida Munnetra Kazhagam 277856 199538 72 43238 22 2011 Maduravoyal 7 GEN Thiruvallur Beem Rao. G Communist Party Of India (MARXIST) 269487 185925 69 24011 13 2011 Ambattur 8 GEN Thiruvallur Vedhachalam. S All India Anna Dravida Munnetra Kazhagam 264960 186347 70 22717 12 2011 Madavaram 9 GEN Thiruvallur Moorthy V All India Anna Dravida Munnetra Kazhagam 275590 207325 75 34765 17 2011 Thiruvottiyur 10 GEN Thiruvallur Kuppan, K. All India Anna Dravida Munnetra Kazhagam 221456 164716 74 27291 17 2011 Dr.Radhakrishnan Nagar 11 GEN Chennai Vetriivel P All India Anna Dravida Munnetra Kazhagam 195146 141942 73 31255 22 2011 Perambur 12 GEN Chennai Soundararajan A Communist Party Of India (MARXIST) 232333 162026 70 17423 11 2011 Kolathur 13 GEN Chennai Stalin M.K. Dravida Munetra Kazhagam 207990 141989 68 2819 2 2011 Villivakkam 14 GEN Chennai Prabhakar Jcd All India Anna Dravida Munnetra Kazhagam 193208 130828 68 10782 8 2011 Thiru-Vi-Ka-Nagar 15 SC Chennai Neelakandan. V All India Anna Dravida Munnetra Kazhagam 181235 123807 68 29341 24 2011 Egmore 16 SC Chennai Nallathambi K Desiya Murpokku Dravida Kazhagam 164759 111996 68 202 0 2011 Royapuram 17 GEN Chennai Jayakumar. D All India Anna Dravida Munnetra Kazhagam 159335 112461 71 21372 19 2011 Harbour 18 GEN Chennai Karuppiah .Pala All India Anna Dravida Munnetra Kazhagam 152784 96475 63 20317 21 2011 Chepauk-Thiruvallikeni 19 GEN Chennai Anbazhagan. J Dravida Munetra Kazhagam 187297 129836 69 9203 7 2011 Thousand Lights 20 GEN Chennai Valarmathi. B All India Anna Dravida Munnetra Kazhagam 199978 133567 67 7592 6 2011 Anna Nagar 21 GEN Chennai Gokula Indira S All India Anna Dravida Munnetra Kazhagam 226816 151608 67 36590 24 2011 Virugampakkam 22 GEN Chennai Partha Sarathy B Desiya Murpokku Dravida Kazhagam 214871 144069 67 14094 10 2011 Saidapet 23 GEN Chennai Senthamizhan.G All India Anna Dravida Munnetra Kazhagam 219001 154225 70 12071 8 2011 Thiyagarayanagar 24 GEN Chennai Kalairajan V P All India Anna Dravida Munnetra Kazhagam 194890 129751 67 32462 25 2011 Mylapore 25 GEN Chennai Rajalakshmi R All India Anna Dravida Munnetra Kazhagam 215336 142882 66 29204 20 2011 Velachery 26 GEN Chennai Ashok M.K. All India Anna Dravida Munnetra Kazhagam 227204 152364 67 31720 21 2011 Shozhinganallur 27 GEN Kancheepuram K.P. Kandan All India Anna Dravida Munnetra Kazhagam 357640 240583 67 66972 28 201

**Final transformation & visualization using powerBI from silver**